In [3]:
! pip install xmltodict

In [4]:
import torch
from transformers import BertTokenizer, BertModel
import xmltodict
from tqdm import tqdm
import numpy as np
import os
import xml.etree.ElementTree as ET

In [5]:
# Initialiser le modèle et le tokenizer BERT
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
tokenizer = BertTokenizer.from_pretrained('bert-large-uncased')
model = BertModel.from_pretrained('bert-large-uncased')
model.to(device)

print(f'Modèle et tokenizer BERT chargés sur {device}.')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/571 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.34G [00:00<?, ?B/s]

Modèle et tokenizer BERT chargés sur cuda.


In [6]:
def open_xml_file(xml_path):
    """
    Charge un fichier XML et retourne sa structure sous forme de dictionnaire.
    """
    with open(xml_path, 'r') as file:
        data = file.read()
    return xmltodict.parse(data)

In [7]:
#data = open_xml_file("/content/semcor.xml")
# Afficher toutes les clés de premier niveau
#print(data.keys())

In [8]:
def collect_sentences_partial(xml_file, max_sentences=1000):
    """
    Collecte une partie des phrases et annotations de sens d'un fichier XML volumineux.

    Args:
        xml_file (str): Chemin vers le fichier XML.
        max_sentences (int): Nombre maximum de phrases à traiter.

    Returns:
        tuple: (sentences, senses, positions)
    """
    sentences, senses, positions = [], [], []
    sentence_count = 0

    # Utiliser iterparse pour parcourir le fichier de manière incrémentale
    context = ET.iterparse(xml_file, events=("start", "end"))
    context = iter(context)
    _, root = next(context)  # Récupérer la racine pour libérer la mémoire

    for event, elem in context:
        if event == "end" and elem.tag == "sentence":  # Traiter chaque phrase
            words = []
            sense_annotations = []
            sense_positions = []

            for i, word in enumerate(elem.findall('word')):
                surface_form = word.get('surface_form', '')
                words.append(surface_form)

                # Vérifier les annotations de sens
                wn16_key = word.get('wn16_key')
                wn30_key = word.get('wn30_key')
                if wn16_key or wn30_key:
                    sense_annotations.append((wn16_key, wn30_key))
                    sense_positions.append(i)
                else:
                    sense_annotations.append(None)

            # Ajouter la phrase à la collection
            sentences.append(words)
            senses.append(sense_annotations)
            positions.append(sense_positions)

            sentence_count += 1
            if sentence_count >= max_sentences:
                break  # Arrêter une fois la limite atteinte

            root.clear()  # Libérer la mémoire pour les éléments déjà traités

    return sentences, senses, positions

In [8]:
# Charger le fichier XML
xml_file = "/content/semcor.xml"
tree = ET.parse("/content/semcor.xml")
root = tree.getroot()

# Parcourir chaque phrase dans le corpus
for sentence in root.iter('sentence'):
    # Extraire les données
    sentences, senses, positions = collect_sentences_partial(xml_file, max_sentences=50)

# Afficher les résultats pour les premières phrases
for i, sentence in enumerate(sentences[:5]):  # Afficher les 5 premières phrases
    print(f"Phrase {i+1}: {sentence}")
    print(f"Sens associés: {senses[i]}")
    print(f"Positions des mots annotés: {positions[i]}")
    print("-" * 50)

In [9]:
def collect_sentences_partial_range(xml_file, start_sentence=1001, max_sentences=500):
    sentences, senses, positions = [], [], []
    sentence_count = 0
    collected_count = 0

    context = ET.iterparse(xml_file, events=("start", "end"))
    context = iter(context)
    _, root = next(context)

    for event, elem in context:
        if event == "end" and elem.tag == "sentence":
            sentence_count += 1

            if sentence_count >= start_sentence:
                words = []
                sense_annotations = []
                sense_positions = []

                for i, word in enumerate(elem.findall('word')):
                    surface_form = word.get('surface_form', '')
                    words.append(surface_form)

                    wn16_key = word.get('wn16_key')
                    wn30_key = word.get('wn30_key')
                    if wn16_key or wn30_key:
                        sense_annotations.append((wn16_key, wn30_key))
                        sense_positions.append(i)
                    else:
                        sense_annotations.append(None)

                sentences.append(words)
                senses.append(sense_annotations)
                positions.append(sense_positions)

                collected_count += 1
                if collected_count >= max_sentences:
                    break

            root.clear()

    return sentences, senses, positions

# Exemple : Extraire les phrases 1001 à 1500
#sentences, senses, positions = collect_sentences_partial_range(
#    "chemin/vers/ton/fichier.xml", start_sentence=1001, max_sentences=500
#)

In [10]:
def get_bert_embeddings(sentence, target_idx):
    """
    Extrait les embeddings BERT pour un mot cible dans une phrase.
    """
    # Convert sentence to string if it's a list
    sentence_str = ' '.join(sentence) if isinstance(sentence, list) else sentence

    # Tokenize with detailed output
    inputs = tokenizer(sentence_str, return_tensors='pt', truncation=True, padding=True)

    # Debug: Print tokenization details
    print("Tokenization Debug:")
    print(f"Original sentence: {sentence_str}")
    print(f"Tokens: {tokenizer.convert_ids_to_tokens(inputs['input_ids'][0])}")
    print(f"Input IDs shape: {inputs['input_ids'].shape}")

    inputs = {key: val.to(device) for key, val in inputs.items()}

    with torch.no_grad():
        outputs = model(**inputs)

    # Debug: Print embedding details
    embeddings = outputs.last_hidden_state.squeeze(0)
    print(f"Embeddings shape: {embeddings.shape}")
    print(f"Target index: {target_idx}")

    return embeddings[target_idx].cpu().numpy()  # Retourner l'embedding du mot cible

In [11]:
def validate_data(sentences, senses, positions):
    """
    Comprehensive validation of input data for WSD.
    """
    print("\n--- Data Validation ---")
    print(f"Total sentences: {len(sentences)}")
    print(f"Total sense annotations: {len(senses)}")
    print(f"Total position lists: {len(positions)}")

    # Check for empty or inconsistent data
    empty_sentences = sum(1 for s in sentences if len(s) == 0)
    empty_senses = sum(1 for s in senses if len(s) == 0)
    empty_positions = sum(1 for p in positions if len(p) == 0)

    print(f"Empty sentences: {empty_sentences}")
    print(f"Empty sense annotations: {empty_senses}")
    print(f"Empty position lists: {empty_positions}")

    # Sample data inspection
    print("\nSample Data:")
    for i in range(min(3, len(sentences))):
        print(f"\nSentence {i+1}:")
        print(f"Words: {sentences[i]}")
        print(f"Senses: {senses[i]}")
        print(f"Annotated Positions: {positions[i]}")

In [12]:
def create_word_sense_maps(sentences, senses, positions):
    """
    Crée des mappages entre les mots, leurs sens et leurs embeddings.
    """
    word_sense_embeddings = {}

    # Validate input data first
    validate_data(sentences, senses, positions)

    for sentence, sentence_senses, pos_list in tqdm(
        zip(sentences, senses, positions),
        desc="Creating Word Sense Embeddings",
        total=len(sentences)
    ):
        for idx in pos_list:
            word = sentence[idx]
            sense = sentence_senses[idx]

            try:
                # Try embedding extraction
                embedding = get_bert_embeddings(sentence, idx)

                if word not in word_sense_embeddings:
                    word_sense_embeddings[word] = {}

                # Accumulate embeddings for the same word-sense pair
                if sense not in word_sense_embeddings[word]:
                    word_sense_embeddings[word][sense] = []

                word_sense_embeddings[word][sense].append(embedding)

            except Exception as e:
                print(f"Error processing word '{word}': {e}")

    # Average embeddings for each word-sense pair
    for word in word_sense_embeddings:
        for sense in word_sense_embeddings[word]:
            word_sense_embeddings[word][sense] = np.mean(
                word_sense_embeddings[word][sense],
                axis=0
            )

    return word_sense_embeddings

In [13]:
# Entraînement : Collecter les embeddings et créer les mappages
def train_model(xml_path):
    xml_data = open_xml_file(xml_path)
    sentences, senses, positions = collect_sentences_partial(xml_path)
    word_sense_maps = create_word_sense_maps(sentences, senses, positions)
    return word_sense_maps

# Test : Évaluation sur des données de test
def test_model(word_sense_maps, test_sentences, test_senses, test_positions):
    correct, total = 0, 0

    for sentence, sentence_senses, pos_list in tqdm(zip(test_sentences, test_senses, test_positions),
                                                    desc="Testing Word Sense Disambiguation",
                                                    total=len(test_sentences)):
        for idx in pos_list:
            word = sentence[idx]
            true_sense = sentence_senses[idx]

            # Get embedding for the current word
            embedding = get_bert_embeddings(sentence, idx)

            if word in word_sense_maps:
                # Compute cosine similarity instead of direct dot product
                similarities = []
                for sense, sense_embedding in word_sense_maps[word].items():
                    # Ensure consistent dimensionality and normalize
                    similarity = np.dot(
                        embedding / np.linalg.norm(embedding),
                        sense_embedding / np.linalg.norm(sense_embedding)
                    )
                    similarities.append((sense, similarity))

                # Find sense with highest similarity
                best_sense = max(similarities, key=lambda x: x[1])[0]

                if best_sense == true_sense:
                    correct += 1
            total += 1

    accuracy = correct / total if total > 0 else 0
    print(f'Accuracy: {accuracy:.2%}')

In [21]:
def split_data(sentences, senses, positions, test_ratio=0.2):
    """
    Split data into training and testing sets with robust handling.

    Args:
        sentences (list): List of sentences
        senses (list): List of sense annotations
        positions (list): List of annotated word positions
        test_ratio (float): Proportion of data to use for testing

    Returns:
        tuple: (train_sentences, train_senses, train_positions,
                test_sentences, test_senses, test_positions)
    """
    import numpy as np

    # Calculate split index
    total_samples = len(sentences)
    split_idx = int(total_samples * (1 - test_ratio))

    # Use list slicing carefully
    train_sentences = list(sentences[:split_idx])
    train_senses = list(senses[:split_idx])
    train_positions = list(positions[:split_idx])

    test_sentences = list(sentences[split_idx:])
    test_senses = list(senses[split_idx:])
    test_positions = list(positions[split_idx:])

    return (train_sentences, train_senses, train_positions,
            test_sentences, test_senses, test_positions)

In [15]:
xml_path = "/content/semcor.xml"
sentences, senses, positions = collect_sentences_partial(xml_path)
validate_data(sentences, senses, positions)


--- Data Validation ---
Total sentences: 1000
Total sense annotations: 1000
Total position lists: 1000
Empty sentences: 0
Empty sense annotations: 0
Empty position lists: 4

Sample Data:

Sentence 1:
Words: ['The', 'Fulton_County_Grand_Jury', 'said', 'Friday', 'an', 'investigation', 'of', 'Atlanta', "'s", 'recent', 'primary_election', 'produced', '"', 'no', 'evidence', '"', 'that', 'any', 'irregularities', 'took_place', '.']
Senses: [None, ('group%1:03:00::', 'group%1:03:00::'), ('say%2:32:00::', 'say%2:32:00::'), ('friday%1:28:00::', 'friday%1:28:00::'), None, ('investigation%1:09:00::', 'investigation%1:09:00::'), None, ('atlanta%1:15:00::', 'atlanta%1:15:00::'), None, ('recent%5:00:00:past:00', 'recent%3:00:00:past:00'), ('primary_election%1:04:00::', 'primary_election%1:04:00::'), ('produce%2:39:01::', 'produce%2:39:01::'), None, None, ('evidence%1:09:00::', 'evidence%1:09:00::'), None, None, None, ('irregularity%1:04:00::', 'irregularity%1:04:00::'), ('take_place%2:30:00::', 'tak

In [16]:
word_sense_maps = create_word_sense_maps(sentences, senses, positions)


--- Data Validation ---
Total sentences: 1000
Total sense annotations: 1000
Total position lists: 1000
Empty sentences: 0
Empty sense annotations: 0
Empty position lists: 4

Sample Data:

Sentence 1:
Words: ['The', 'Fulton_County_Grand_Jury', 'said', 'Friday', 'an', 'investigation', 'of', 'Atlanta', "'s", 'recent', 'primary_election', 'produced', '"', 'no', 'evidence', '"', 'that', 'any', 'irregularities', 'took_place', '.']
Senses: [None, ('group%1:03:00::', 'group%1:03:00::'), ('say%2:32:00::', 'say%2:32:00::'), ('friday%1:28:00::', 'friday%1:28:00::'), None, ('investigation%1:09:00::', 'investigation%1:09:00::'), None, ('atlanta%1:15:00::', 'atlanta%1:15:00::'), None, ('recent%5:00:00:past:00', 'recent%3:00:00:past:00'), ('primary_election%1:04:00::', 'primary_election%1:04:00::'), ('produce%2:39:01::', 'produce%2:39:01::'), None, None, ('evidence%1:09:00::', 'evidence%1:09:00::'), None, None, None, ('irregularity%1:04:00::', 'irregularity%1:04:00::'), ('take_place%2:30:00::', 'tak

Creating Word Sense Embeddings:   0%|          | 0/1000 [00:00<?, ?it/s]

Tokenization Debug:
Original sentence: The Fulton_County_Grand_Jury said Friday an investigation of Atlanta 's recent primary_election produced " no evidence " that any irregularities took_place .
Tokens: ['[CLS]', 'the', 'fulton', '_', 'county', '_', 'grand', '_', 'jury', 'said', 'friday', 'an', 'investigation', 'of', 'atlanta', "'", 's', 'recent', 'primary', '_', 'election', 'produced', '"', 'no', 'evidence', '"', 'that', 'any', 'irregularities', 'took', '_', 'place', '.', '[SEP]']
Input IDs shape: torch.Size([1, 34])
Embeddings shape: torch.Size([34, 1024])
Target index: 1
Tokenization Debug:
Original sentence: The Fulton_County_Grand_Jury said Friday an investigation of Atlanta 's recent primary_election produced " no evidence " that any irregularities took_place .
Tokens: ['[CLS]', 'the', 'fulton', '_', 'county', '_', 'grand', '_', 'jury', 'said', 'friday', 'an', 'investigation', 'of', 'atlanta', "'", 's', 'recent', 'primary', '_', 'election', 'produced', '"', 'no', 'evidence', '"

Creating Word Sense Embeddings:   0%|          | 1/1000 [00:01<32:50,  1.97s/it]

Embeddings shape: torch.Size([34, 1024])
Target index: 14
Tokenization Debug:
Original sentence: The Fulton_County_Grand_Jury said Friday an investigation of Atlanta 's recent primary_election produced " no evidence " that any irregularities took_place .
Tokens: ['[CLS]', 'the', 'fulton', '_', 'county', '_', 'grand', '_', 'jury', 'said', 'friday', 'an', 'investigation', 'of', 'atlanta', "'", 's', 'recent', 'primary', '_', 'election', 'produced', '"', 'no', 'evidence', '"', 'that', 'any', 'irregularities', 'took', '_', 'place', '.', '[SEP]']
Input IDs shape: torch.Size([1, 34])
Embeddings shape: torch.Size([34, 1024])
Target index: 18
Tokenization Debug:
Original sentence: The Fulton_County_Grand_Jury said Friday an investigation of Atlanta 's recent primary_election produced " no evidence " that any irregularities took_place .
Tokens: ['[CLS]', 'the', 'fulton', '_', 'county', '_', 'grand', '_', 'jury', 'said', 'friday', 'an', 'investigation', 'of', 'atlanta', "'", 's', 'recent', 'prima

...

Embeddings shape: torch.Size([40, 1024])
Target index: 17
Tokenization Debug:
Original sentence: If , in Larkin 's eyes , they are nothing but Piccadilly farmers , he has as much to learn about them as they have to learn about the ways of truly rural living .
Tokens: ['[CLS]', 'if', ',', 'in', 'larkin', "'", 's', 'eyes', ',', 'they', 'are', 'nothing', 'but', 'pic', '##ca', '##dilly', 'farmers', ',', 'he', 'has', 'as', 'much', 'to', 'learn', 'about', 'them', 'as', 'they', 'have', 'to', 'learn', 'about', 'the', 'ways', 'of', 'truly', 'rural', 'living', '.', '[SEP]']
Input IDs shape: torch.Size([1, 40])
Embeddings shape: torch.Size([40, 1024])
Target index: 19
Tokenization Debug:
Original sentence: If , in Larkin 's eyes , they are nothing but Piccadilly farmers , he has as much to learn about them as they have to learn about the ways of truly rural living .
Tokens: ['[CLS]', 'if', ',', 'in', 'larkin', "'", 's', 'eyes', ',', 'they', 'are', 'nothing', 'but', 'pic', '##ca', '##dilly', 'farm

Creating Word Sense Embeddings: 100%|█████████▉| 999/1000 [03:54<00:00,  4.44it/s]

Embeddings shape: torch.Size([17, 1024])
Target index: 1
Tokenization Debug:
Original sentence: Mr._Bates shows us how this mutual education spreads its inevitable havoc .
Tokens: ['[CLS]', 'mr', '.', '_', 'bates', 'shows', 'us', 'how', 'this', 'mutual', 'education', 'spreads', 'its', 'inevitable', 'havoc', '.', '[SEP]']
Input IDs shape: torch.Size([1, 17])
Embeddings shape: torch.Size([17, 1024])
Target index: 5
Tokenization Debug:
Original sentence: Mr._Bates shows us how this mutual education spreads its inevitable havoc .
Tokens: ['[CLS]', 'mr', '.', '_', 'bates', 'shows', 'us', 'how', 'this', 'mutual', 'education', 'spreads', 'its', 'inevitable', 'havoc', '.', '[SEP]']
Input IDs shape: torch.Size([1, 17])
Embeddings shape: torch.Size([17, 1024])
Target index: 6
Tokenization Debug:
Original sentence: Mr._Bates shows us how this mutual education spreads its inevitable havoc .
Tokens: ['[CLS]', 'mr', '.', '_', 'bates', 'shows', 'us', 'how', 'this', 'mutual', 'education', 'spreads', '

Creating Word Sense Embeddings: 100%|██████████| 1000/1000 [03:54<00:00,  4.26it/s]


Embeddings shape: torch.Size([15, 1024])
Target index: 8
Tokenization Debug:
Original sentence: Oneupmanship is practiced by both sides in a total war .
Tokens: ['[CLS]', 'one', '##up', '##manship', 'is', 'practiced', 'by', 'both', 'sides', 'in', 'a', 'total', 'war', '.', '[SEP]']
Input IDs shape: torch.Size([1, 15])
Embeddings shape: torch.Size([15, 1024])
Target index: 9


In [19]:
# Verify the created word sense maps
print("Word Sense Maps Statistics:")
print(f"Total unique words: {len(word_sense_maps)}")
print("Sample word sense embeddings:")
for word, senses in list(word_sense_maps.items())[:3]:
    print(f"{word}: {len(senses)} unique senses")

Word Sense Maps Statistics:
Total unique words: 4808
Sample word sense embeddings:
Fulton_County_Grand_Jury: 1 unique senses
said: 2 unique senses
Friday: 1 unique senses


In [23]:
def investigate_data_structure(sentences, senses, positions):
    """
    Thoroughly investigate the data structure to diagnose splitting issues.
    """
    print("Data Structure Investigation:")
    print(f"Type of sentences: {type(sentences)}")
    print(f"Type of senses: {type(senses)}")
    print(f"Type of positions: {type(positions)}")

    # Check if the data is nested or has an unexpected structure
    print("\nSample Data:")
    try:
        print(f"First sentence: {sentences[0]}")
        print(f"First sense annotation: {senses[0]}")
        print(f"First position list: {positions[0]}")
    except Exception as e:
        print(f"Error accessing first elements: {e}")

    # Attempt to convert to list if not already
    try:
        sentences_list = list(sentences)
        senses_list = list(senses)
        positions_list = list(positions)

        print("\nSuccessful List Conversion:")
        print(f"Sentences list length: {len(sentences_list)}")
        print(f"Senses list length: {len(senses_list)}")
        print(f"Positions list length: {len(positions_list)}")

        return sentences_list, senses_list, positions_list
    except Exception as e:
        print(f"Conversion to list failed: {e}")
        return None, None, None

# Execute the investigation
xml_path = "/content/semcor.xml"
sentences, senses, positions = collect_sentences_partial(xml_path)
investigated_sentences, investigated_senses, investigated_positions = investigate_data_structure(
    sentences, senses, positions
)

Data Structure Investigation:
Type of sentences: <class 'list'>
Type of senses: <class 'list'>
Type of positions: <class 'list'>

Sample Data:
First sentence: ['The', 'Fulton_County_Grand_Jury', 'said', 'Friday', 'an', 'investigation', 'of', 'Atlanta', "'s", 'recent', 'primary_election', 'produced', '"', 'no', 'evidence', '"', 'that', 'any', 'irregularities', 'took_place', '.']
First sense annotation: [None, ('group%1:03:00::', 'group%1:03:00::'), ('say%2:32:00::', 'say%2:32:00::'), ('friday%1:28:00::', 'friday%1:28:00::'), None, ('investigation%1:09:00::', 'investigation%1:09:00::'), None, ('atlanta%1:15:00::', 'atlanta%1:15:00::'), None, ('recent%5:00:00:past:00', 'recent%3:00:00:past:00'), ('primary_election%1:04:00::', 'primary_election%1:04:00::'), ('produce%2:39:01::', 'produce%2:39:01::'), None, None, ('evidence%1:09:00::', 'evidence%1:09:00::'), None, None, None, ('irregularity%1:04:00::', 'irregularity%1:04:00::'), ('take_place%2:30:00::', 'take_place%2:30:00::'), None]
First 

In [24]:
# Split the data into training and testing sets
try:
    (train_sentences, train_senses, train_positions,
     test_sentences, test_senses, test_positions) = split_data(
        sentences, senses, positions, test_ratio=0.2
    )

    print("Data Split Successful:")
    print(f"Training set size: {len(train_sentences)} sentences")
    print(f"Testing set size: {len(test_sentences)} sentences")

    # Additional verification
    print("\nTraining Data Sample:")
    print(f"First training sentence: {train_sentences[0]}")
    print(f"Corresponding senses: {train_senses[0]}")
    print(f"Annotated positions: {train_positions[0]}")

except Exception as e:
    print(f"Error during data splitting: {e}")

Data Split Successful:
Training set size: 800 sentences
Testing set size: 200 sentences

Training Data Sample:
First training sentence: ['The', 'Fulton_County_Grand_Jury', 'said', 'Friday', 'an', 'investigation', 'of', 'Atlanta', "'s", 'recent', 'primary_election', 'produced', '"', 'no', 'evidence', '"', 'that', 'any', 'irregularities', 'took_place', '.']
Corresponding senses: [None, ('group%1:03:00::', 'group%1:03:00::'), ('say%2:32:00::', 'say%2:32:00::'), ('friday%1:28:00::', 'friday%1:28:00::'), None, ('investigation%1:09:00::', 'investigation%1:09:00::'), None, ('atlanta%1:15:00::', 'atlanta%1:15:00::'), None, ('recent%5:00:00:past:00', 'recent%3:00:00:past:00'), ('primary_election%1:04:00::', 'primary_election%1:04:00::'), ('produce%2:39:01::', 'produce%2:39:01::'), None, None, ('evidence%1:09:00::', 'evidence%1:09:00::'), None, None, None, ('irregularity%1:04:00::', 'irregularity%1:04:00::'), ('take_place%2:30:00::', 'take_place%2:30:00::'), None]
Annotated positions: [1, 2, 3, 

In [25]:
# Test the model using the created word sense maps
test_model(
    word_sense_maps,
    test_sentences,
    test_senses,
    test_positions
)

Testing Word Sense Disambiguation:   0%|          | 1/200 [00:00<00:27,  7.24it/s]

Tokenization Debug:
Original sentence: She should offer substitutes for the temptations which seem overwhelmingly desirable to the child .
Tokens: ['[CLS]', 'she', 'should', 'offer', 'substitutes', 'for', 'the', 'temptation', '##s', 'which', 'seem', 'overwhelmingly', 'desirable', 'to', 'the', 'child', '.', '[SEP]']
Input IDs shape: torch.Size([1, 18])
Embeddings shape: torch.Size([18, 1024])
Target index: 2
Tokenization Debug:
Original sentence: She should offer substitutes for the temptations which seem overwhelmingly desirable to the child .
Tokens: ['[CLS]', 'she', 'should', 'offer', 'substitutes', 'for', 'the', 'temptation', '##s', 'which', 'seem', 'overwhelmingly', 'desirable', 'to', 'the', 'child', '.', '[SEP]']
Input IDs shape: torch.Size([1, 18])
Embeddings shape: torch.Size([18, 1024])
Target index: 3
Tokenization Debug:
Original sentence: She should offer substitutes for the temptations which seem overwhelmingly desirable to the child .
Tokens: ['[CLS]', 'she', 'should', 'off

Testing Word Sense Disambiguation:   1%|          | 2/200 [00:00<00:30,  6.51it/s]

Embeddings shape: torch.Size([24, 1024])
Target index: 11
Tokenization Debug:
Original sentence: If he can't play with Mommy 's magazines , he should have some old numbers of his own .
Tokens: ['[CLS]', 'if', 'he', 'can', "'", 't', 'play', 'with', 'mommy', "'", 's', 'magazines', ',', 'he', 'should', 'have', 'some', 'old', 'numbers', 'of', 'his', 'own', '.', '[SEP]']
Input IDs shape: torch.Size([1, 24])
Embeddings shape: torch.Size([24, 1024])
Target index: 12
Tokenization Debug:
Original sentence: If he can't play with Mommy 's magazines , he should have some old numbers of his own .
Tokens: ['[CLS]', 'if', 'he', 'can', "'", 't', 'play', 'with', 'mommy', "'", 's', 'magazines', ',', 'he', 'should', 'have', 'some', 'old', 'numbers', 'of', 'his', 'own', '.', '[SEP]']
Input IDs shape: torch.Size([1, 24])
Embeddings shape: torch.Size([24, 1024])
Target index: 13
Tokenization Debug:
Original sentence: If he can't play with Mommy 's magazines , he should have some old numbers of his own .
Tok

Testing Word Sense Disambiguation:   2%|▏         | 3/200 [00:00<00:29,  6.64it/s]

...

Embeddings shape: torch.Size([23, 1024])
Target index: 1
Tokenization Debug:
Original sentence: They plan to become county people who know the proper way to terminate a fox 's life on earth .
Tokens: ['[CLS]', 'they', 'plan', 'to', 'become', 'county', 'people', 'who', 'know', 'the', 'proper', 'way', 'to', 'terminate', 'a', 'fox', "'", 's', 'life', 'on', 'earth', '.', '[SEP]']
Input IDs shape: torch.Size([1, 23])
Embeddings shape: torch.Size([23, 1024])
Target index: 3
Tokenization Debug:
Original sentence: They plan to become county people who know the proper way to terminate a fox 's life on earth .
Tokens: ['[CLS]', 'they', 'plan', 'to', 'become', 'county', 'people', 'who', 'know', 'the', 'proper', 'way', 'to', 'terminate', 'a', 'fox', "'", 's', 'life', 'on', 'earth', '.', '[SEP]']
Input IDs shape: torch.Size([1, 23])
Embeddings shape: torch.Size([23, 1024])
Target index: 4
Tokenization Debug:
Original sentence: They plan to become county people who know the proper way to terminate a

Testing Word Sense Disambiguation: 100%|█████████▉| 199/200 [00:40<00:00,  6.03it/s]

Tokens: ['[CLS]', 'if', ',', 'in', 'larkin', "'", 's', 'eyes', ',', 'they', 'are', 'nothing', 'but', 'pic', '##ca', '##dilly', 'farmers', ',', 'he', 'has', 'as', 'much', 'to', 'learn', 'about', 'them', 'as', 'they', 'have', 'to', 'learn', 'about', 'the', 'ways', 'of', 'truly', 'rural', 'living', '.', '[SEP]']
Input IDs shape: torch.Size([1, 40])
Embeddings shape: torch.Size([40, 1024])
Target index: 31
Tokenization Debug:
Original sentence: If , in Larkin 's eyes , they are nothing but Piccadilly farmers , he has as much to learn about them as they have to learn about the ways of truly rural living .
Tokens: ['[CLS]', 'if', ',', 'in', 'larkin', "'", 's', 'eyes', ',', 'they', 'are', 'nothing', 'but', 'pic', '##ca', '##dilly', 'farmers', ',', 'he', 'has', 'as', 'much', 'to', 'learn', 'about', 'them', 'as', 'they', 'have', 'to', 'learn', 'about', 'the', 'ways', 'of', 'truly', 'rural', 'living', '.', '[SEP]']
Input IDs shape: torch.Size([1, 40])
Embeddings shape: torch.Size([40, 1024])
Tar

Testing Word Sense Disambiguation: 100%|██████████| 200/200 [00:40<00:00,  4.94it/s]

Embeddings shape: torch.Size([15, 1024])
Target index: 0
Tokenization Debug:
Original sentence: Oneupmanship is practiced by both sides in a total war .
Tokens: ['[CLS]', 'one', '##up', '##manship', 'is', 'practiced', 'by', 'both', 'sides', 'in', 'a', 'total', 'war', '.', '[SEP]']
Input IDs shape: torch.Size([1, 15])
Embeddings shape: torch.Size([15, 1024])
Target index: 2
Tokenization Debug:
Original sentence: Oneupmanship is practiced by both sides in a total war .
Tokens: ['[CLS]', 'one', '##up', '##manship', 'is', 'practiced', 'by', 'both', 'sides', 'in', 'a', 'total', 'war', '.', '[SEP]']
Input IDs shape: torch.Size([1, 15])
Embeddings shape: torch.Size([15, 1024])
Target index: 5
Tokenization Debug:
Original sentence: Oneupmanship is practiced by both sides in a total war .
Tokens: ['[CLS]', 'one', '##up', '##manship', 'is', 'practiced', 'by', 'both', 'sides', 'in', 'a', 'total', 'war', '.', '[SEP]']
Input IDs shape: torch.Size([1, 15])
Embeddings shape: torch.Size([15, 1024])
Ta